In [7]:
import json
import os
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [8]:
# ===== 用户可调整的参数 =====
root_data_dir = "C:/Users/96412/AppData/LocalLow/DefaultCompany/VRTheatre/TrailData"   # 根数据目录，里面是多个以用户名开头的子文件夹
user_name     = "Lucas"    # 只处理文件夹名以此开头的目录
time_tolerance = 0.5       # 秒级匹配容差

In [9]:
# 遍历所有子目录，筛选出以 user_name 开头的文件夹
session_dirs = [
    d for d in os.listdir(root_data_dir)
    if d.startswith(user_name) and os.path.isdir(os.path.join(root_data_dir, d))
]

for session in session_dirs:
    session_path = os.path.join(root_data_dir, session)
    horiz_path = os.path.join(session_path, "Horizontal.json")
    vert_path  = os.path.join(session_path, "Vertical.json")
    if not (os.path.isfile(horiz_path) and os.path.isfile(vert_path)):
        print(f"跳过 {session}：缺少 Horizontal.json 或 Vertical.json")
        continue

    # 读取并排序
    with open(horiz_path, "r") as f:
        horiz_data = json.load(f)["points"]
    with open(vert_path, "r") as f:
        vert_data  = json.load(f)["points"]
    horiz_data.sort(key=lambda x: x["time"])
    vert_data.sort(key=lambda x: x["time"])

    # 从 JSON 读取视频总时长
    with open(horiz_path, "r") as f:
        video_duration = json.load(f).get("videoDuration", 0)
    total_seconds = int(video_duration) + 1

    # 时间对齐
    i, j = 0, 0
    matched = []
    while i < len(horiz_data) and j < len(vert_data):
        t_h, t_v = horiz_data[i]["time"], vert_data[j]["time"]
        if abs(t_h - t_v) <= time_tolerance:
            matched.append(((t_h + t_v) / 2, horiz_data[i]["angle"], vert_data[j]["angle"]))
            i += 1; j += 1
        elif t_h < t_v:
            i += 1
        else:
            j += 1

    # 构建热力图矩阵
    h_min, h_max = -180, 180
    v_min, v_max =  -90,  90
    h_cols = h_max - h_min + 1
    v_cols = v_max - v_min + 1

    heat_h = [[0]*h_cols for _ in range(total_seconds)]
    heat_v = [[0]*v_cols for _ in range(total_seconds)]
    text_h = [[""]*h_cols for _ in range(total_seconds)]
    text_v = [[""]*v_cols for _ in range(total_seconds)]

    for t, ha, va in matched:
        ti = int(t)
        hi = max(h_min, min(h_max, int(round(ha))))
        vi = max(v_min, min(v_max, int(round(va))))
        ci_h, ci_v = hi - h_min, vi - v_min
        heat_h[ti][ci_h] += 1
        heat_v[ti][ci_v] += 1
        txt = f"时间: {t:.2f}秒  |  水平: {hi}°  |  垂直: {vi}°"
        text_h[ti][ci_h] = txt
        text_v[ti][ci_v] = txt

    # 绘图
    fig = make_subplots(
        rows=2, cols=3,
        specs=[[None, {"type":"heatmap"}, None],
               [{"colspan":3,"type":"heatmap"}, None, None]],
        column_widths=[0.4,0.2,0.4],
        row_heights=[0.7,0.3],
        vertical_spacing=0.02
    )

    fig.add_trace(go.Heatmap(
        z=heat_h, x=list(range(h_min,h_max+1)), y=list(range(total_seconds)),
        text=text_h, hoverinfo="text",
        colorscale=[[0,"white"],[0.5,"yellow"],[1,"red"]],
        zmin=0, zmax=max(1,max(map(max,heat_h))),
        colorbar=dict(title="热度",len=0.5,x=0.95,y=0.75)
    ), row=1, col=2)

    fig.add_trace(go.Heatmap(
        z=heat_v, x=list(range(v_min,v_max+1)), y=list(range(total_seconds)),
        text=text_v, hoverinfo="text",
        colorscale=[[0,"white"],[0.5,"yellow"],[1,"red"]],
        zmin=0, zmax=max(1,max(map(max,heat_v))),
        showscale=False
    ), row=2, col=1)

    fig.update_xaxes(title_text="水平角度 (°)", range=[h_min,h_max], row=1, col=2)
    fig.update_xaxes(title_text="垂直角度 (°)", range=[v_min,v_max], row=2, col=1)
    fig.update_yaxes(title_text="时间 (秒)", autorange="reversed", row=2, col=1)
    fig.update_yaxes(showticklabels=False, row=1, col=2)

    fig.update_layout(
        title_text=f"用户 {user_name} — 会话 {session} 热力图",
        height=600, width=900,
        margin=dict(t=50,b=40)
    )
    fig.show()